In [1]:
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize
from matplotlib import rc, animation, cm
import numpy as np
from scipy.integrate import quad
from IPython.display import HTML, Image

#change the color/style parameters to your liking
rc("figure",figsize=(4,4),facecolor='202020')
rc("axes", facecolor='202020')
plt.style.use(['dark_background'])
x = np.linspace(0,2,100)
y = np.linspace(0,2,100)

# Implementing Higher-Dimensional Methods
## General Form
Systems of hyperbolic conservation laws in multiple spatial dimensions $\mathbf{x}\in\mathbb{R}^d$ and one time dimension $t\in\mathbb{R}^{+}$ for the unknown $\mathbf{U}\in\mathbb{R}^n$ have the following form:

$$\begin{gather*}
\partial_t\mathbf{U} + \partial_x\mathbf{F}^{(1)}(\mathbf{U}) + \partial_x\mathbf{F}^{(2)}(\mathbf{U}) + ... = 0
\end{gather*}$$

We can write the flux function as a matrix-valued flux $\mathcal{F} \in \mathbb{R}^n\times\mathbb{R}^d$:

$$\begin{gather*}
\mathcal{F} = \begin{pmatrix}\mathbf{F}^{(1)}_1 & \mathbf{F}^{(2)}_1 & \\ \mathbf{F}^{(1)}_2 & \mathbf{F}^{(2)}_2 & \cdots \\ & \vdots & \end{pmatrix}
\end{gather*}$$

The system of conservation laws can then be expressed easily and concisely, using the [divergence operator](https://en.wikipedia.org/wiki/Divergence#Tensor_field):

$$\begin{gather*}
\partial_t\mathbf{U} + \operatorname{div}\mathcal{F}(\mathbf{U}) = 0
\end{gather*}$$

---
### Example 1: 2D Advection
Consider an extension of the 1-d advection problem, with 2-dimensional advection in the direction $(a,b)\in\mathbb{R}^2$. The conservation law for this problem reads:

$$\begin{align*}
\partial_tu + \nabla\cdot\left(au\;bu\right) &= 0\\
\partial_tu + a\partial_xu + b\partial_yu &= 0, (x,y)\in{\mathbb{R}^2},\;t\gt0,\;u(x,y,0) = u_0(x,y)
\end{align*}$$

The analytical solution to this problem is $u(x,y,t) = u_0(x-at,y-bt)$, since we are easily able to solve this problem by the method of characteristics.

In [2]:
%matplotlib agg
u_0 = lambda x, y: np.sin(2*np.pi*(x+y))
a = 1
b = 1
fig,ax = plt.subplots()
fig.suptitle("2D advection with v=({},{})".format(a,b))
X, Y = np.meshgrid(x, y)
def animate(dt, tsteps):
    t = 0
    while t<=tsteps:
        yield (ax.imshow(u_0(X-a*t*dt,Y-b*t*dt),cmap=cm.viridis, origin='lower',extent=[0,2,0,2],vmax=1,vmin=-1),)
        t += 1
advec_anim = animation.ArtistAnimation(fig, [a for a in animate(0.05, 60)], interval=100)
#fig.colorbar(cm.ScalarMappable(Normalize(vmin=-1,vmax=1),cmap=cm.viridis),ax)
HTML(advec_anim.to_jshtml())

---
## Splitting Methods
Practically all realistic applications involve multiple operators. For example, multi-dimensional conservation laws, such as the one above with $d=2$ can be written with _evolution operators_ $\mathcal{A}$ and $\mathcal{B}$:

$$\begin{gather*} \mathcal{A}(u) = -a\partial_xu,\; \mathcal{B} = -b\partial_yu \end{gather*}$$

This then allows the consideration of a very general form of a PDE:

$$\begin{gather*} \partial_tu = \mathcal{A}(u)+\mathcal{B}(u)\end{gather*}$$

Relaxational balance laws add an algebraic right-hand side $P(u)$

$$\begin{gather*}\partial_tu + \partial_xf(u) = P(u)\\\mathcal{A}(u)=-\partial_xf(u), \; \mathcal{B}(u) = P(u)\end{gather*}$$

---

### Example 2: Relaxational Balance Law
We start with the simplest relaxational balance law, and solve it via the method of characteristics:

$$\begin{gather*} \partial_tu + a\partial_xu = -\beta u\end{gather*}$$

Suppose $u(x,t) = u(x(s), t(s))$ and that $x = as$ and $t = s$. Then

$$\begin{align*}\frac{\partial u}{\partial t}\frac{\partial t}{\partial s} + \frac{\partial u}{\partial x}\frac{\partial x}{\partial s} &= -\beta u\\u(x(s),t(s)) &= u_0e^{-\beta t}\\u(x,t)&=u_0(x-at)e^{-\beta t}\end{align*}$$


In [3]:
u_0 = lambda x: np.sin(np.pi*x/2)
fig,ax = plt.subplots()
ax.set_xlim(-2,2)
ax.set_ylim(-1.1,1.1)
x = np.linspace(-2,2,200)
a = 1
beta = 1
fig.suptitle("Relaxational Balance")
def animate(dt, tsteps):
    t = 0
    while t<=tsteps:
        yield (*ax.plot(x,u_0(x-a*t*dt)*np.exp(-beta*t*dt),c=cm.tab10.colors[0]),)
        t += 1
advec_anim = animation.ArtistAnimation(fig, [a for a in animate(0.01, 150)], interval=60)
#fig.colorbar(cm.ScalarMappable(Normalize(vmin=-1,vmax=1),cmap=cm.viridis),ax)
HTML(advec_anim.to_jshtml())